In [2]:
import pandas as pd
import numpy as np
from catboost import CatBoostRegressor
import joblib
import time
from tqdm import tqdm
import os
import warnings
warnings.filterwarnings('ignore') #warning 문구 제거
pd.set_option('display.max_columns', None)

In [3]:
#데이터 불러오기
path = './bami/data/total/'
# path = 'C:/Users/psj70/Desktop/권역별 4개 모델(0225공유)/권역별 4개 모델(0225공유)'
visit_area_info = pd.read_csv(os.path.join(path, '방문지정보.csv')) # 방문지 정보 activity
travel = pd.read_csv(os.path.join(path, '여행.csv')) # 여행 travel
traveller_master = pd.read_csv(os.path.join(path, '여행객 Master.csv')) #여행객 정보 Master traveler

# 전처리

## 1) visit_area_info 방문지 정보 df

In [4]:
# 관광지 선택
visit_area_info = visit_area_info[ (visit_area_info['VISIT_AREA_TYPE_CD'] == 1) | 
                                  (visit_area_info['VISIT_AREA_TYPE_CD'] == 2) |
           (visit_area_info['VISIT_AREA_TYPE_CD'] == 3) | (visit_area_info['VISIT_AREA_TYPE_CD'] == 4) |
           (visit_area_info['VISIT_AREA_TYPE_CD'] == 5) | (visit_area_info['VISIT_AREA_TYPE_CD'] == 6) |
            (visit_area_info['VISIT_AREA_TYPE_CD'] == 7) | (visit_area_info['VISIT_AREA_TYPE_CD'] == 8)]

In [5]:
#인덱스 재정렬
visit_area_info = visit_area_info.reset_index(drop = True)

In [6]:
#제대로 추출되었는지 확인
visit_area_info['VISIT_AREA_TYPE_CD'].unique()

array([2, 1, 6, 4, 3, 7, 5, 8], dtype=int64)

In [7]:
visit_area_info.dropna(subset = ['LOTNO_ADDR'], inplace = True)
visit_area_info = visit_area_info.reset_index(drop = True)

In [8]:
# 시도/군구 변수 생성
sido = []
gungu = []
for i in range(len(visit_area_info['LOTNO_ADDR'])):
    sido.append(visit_area_info['LOTNO_ADDR'][i].split(' ')[0])
    gungu.append(visit_area_info['LOTNO_ADDR'][i].split(' ')[1])

In [9]:
visit_area_info['SIDO'] = sido
visit_area_info['GUNGU'] = gungu

In [10]:
visit_area_info['SIDO'].value_counts()

SIDO
경기         3232
서울         2328
경북         2223
전북         1719
충남         1688
강원특별자치도    1662
전남         1660
부산         1552
강원         1178
대전         1143
충북         1124
경남         1028
인천          571
대구          441
광주          295
울산          273
세종특별자치시     218
강원도           5
경상북도          4
전라북도          3
경기도           3
부산광역시         3
충청남도          3
전라남도          2
충청북도          2
서울특별시         1
경상남도          1
Name: count, dtype: int64

### 변수 선택

TRAVEL_ID 여행 ID

VISIT_AREA_NM 방문 장소 이름

SIDO 시/도

GUNGU 군/구

VISIT_AREA_TYPE_CD 관광 장소 유형

DGSTFN 만족도

REVISIT_INTENTION 재방문의향

RCMDTN_INTENTION 추천의향

RESIDENCE_TIME_MIN 체류시간분

REVISIT_YN 재방문여부

In [11]:
visit_area_info = visit_area_info[['TRAVEL_ID', 'VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD', 'DGSTFN',
                                  'REVISIT_INTENTION', 'RCMDTN_INTENTION', 'RESIDENCE_TIME_MIN', 'REVISIT_YN']]

## 2) travel 여행 정보 df

In [12]:
# TRAVEL_MISSION_CHECK의 첫번째 항목 가져오기
travel_list = []
for i in range(len(travel)):
    value = int(travel['TRAVEL_MISSION_CHECK'][i].split(';')[0])
    travel_list.append(value)

travel['TRAVEL_MISSION_PRIORITY'] = travel_list

### 변수 선택

TRAVEL_ID: 여행 ID

TRAVELER_ID: 여행자 ID

TRAVEL_MISSION_PRIORITY: 개별 미션 우선도 중 첫번째

In [13]:
travel = travel[['TRAVEL_ID', 'TRAVELER_ID', 'TRAVEL_MISSION_PRIORITY']]

## 3) traveller_master 여행자 정보 df

### 변수 선택

TRAVELER_ID 여행객ID

GENDER 성별

AGE_GRP 연령대

INCOME 소득

TRAVEL_STYL(1,2,3,4,5,6,7,8) 여행 스타일 

TRAVEL_MOVTIVE(1) 여행 동기 - 2,3은 결측치가 있어 제외

TRAVEL_NUM 여행빈도

TRAVEL_COMPANIONS_NUM 동반자 수


In [14]:
traveller_master = traveller_master[['TRAVELER_ID', 'GENDER', 'AGE_GRP', 'INCOME', 'TRAVEL_STYL_1', 
                                     'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4', 'TRAVEL_STYL_5', 
                                     'TRAVEL_STYL_6', 'TRAVEL_STYL_7','TRAVEL_STYL_8', 
                                      'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM' ]]

## 데이터 프레임 합치기

In [15]:
df = pd.merge(travel, traveller_master, left_on = 'TRAVELER_ID', right_on = 'TRAVELER_ID', how = 'inner')

In [16]:
df = pd.merge(visit_area_info, df, left_on = 'TRAVEL_ID', right_on = 'TRAVEL_ID', how = 'right')

## 만족도(y) 결측치 삭제

In [17]:
df = df.dropna(subset = ['DGSTFN'])
df.reset_index(drop=True, inplace=True)

## 체류시간 결측치 대체


체류시간 0을 median 60으로 바꾸기

In [18]:
df['RESIDENCE_TIME_MIN'] = df['RESIDENCE_TIME_MIN'].replace(0,60)

## 재방문여부 원핫인코딩

In [19]:
df['REVISIT_YN'] = df['REVISIT_YN'].replace("N",0)
df['REVISIT_YN'] = df['REVISIT_YN'].replace("Y",1)

## 여행스타일 결측치 삭제

In [20]:
df.dropna(subset = ['TRAVEL_STYL_1'], inplace = True)
df.reset_index(drop= True, inplace = True)

## 여행 목적 결측치 삭제

In [21]:
df.dropna(subset = ['TRAVEL_MOTIVE_1'], inplace = True)
df.reset_index(drop= True, inplace = True)

In [22]:
df.shape

(22362, 26)

In [23]:
df.isna().sum().sum()

0

# Train-test split

-유니크한 관광지 정보가 모두 train set에 있어야 한다. (train set에 경복궁 없고 test set에만 경복궁 있으면 안된다. 왜냐하면 방문지 변수가 있기 때문에 입력되지 않은 방문지에 대한 정보는 모델이 학습할 수 없기 때문이다.)

-또한 새로운 유저에 대한 추측이기 때문에 유저 데이터는 무조건 train / test 중 한 곳에만 있다. (유저 A의 ㄱ관광지는 train, ㄴ관광지는 test 에 있을 수 없다.)

-이를 반영해서 train test split 진행하면 된다. 

-train set에서만 (방문지마다 체류시간 평균, 추천의향의 평균, 재방문여부의 평균, 동반자 수의 평균, 재방문의향의 평균)을 산출하고, 이 값을 test set에 대입한다. 

In [25]:
from tqdm import tqdm
df1 = df
Train = pd.DataFrame(columns = list(df.columns))
for i in tqdm(list(df['VISIT_AREA_NM'].unique())): # 유니크한 관광지 목록 중에서
    df2 = df1[df1['VISIT_AREA_NM'] == i] # 특정 관광지에 간 모든 사람 뽑아서
    np.random.seed(42)
    if df2.empty:
        pass
    else:
        random_number = np.random.randint(len(df2)) 
        df_id = df2.iloc[[random_number]] # 그 중 랜덤으로 관광지에 간 사람 한 명 뽑아서
        index = df_id.iloc[0,0]
        df3 = df1[df1['TRAVEL_ID'] == index] #그 사람이 간 모든 관광지를 구해서
        df1 = pd.merge(df3, df1, how = 'outer', indicator = True)
        df1 = df1.query('_merge =="right_only"').drop(columns = ['_merge']) # 기존 데이터프레임에서 그 사람 내용을 삭제하고
        # Train = Train.append(df3) #train set 에 추가
        Train = pd.concat([Train, df3])
'''        
이 프로세스를 바복하면 전체 데이터프레임(df)에 유저정보는 계속해서 삭제될 것이고, 남은 df가 test set,
Train 데이터프레임이 train set이 되는 것임
'''

  0%|          | 0/8805 [00:00<?, ?it/s]

100%|██████████| 8805/8805 [05:40<00:00, 25.86it/s] 


'        \n이 프로세스를 바복하면 전체 데이터프레임(df)에 유저정보는 계속해서 삭제될 것이고, 남은 df가 test set,\nTrain 데이터프레임이 train set이 되는 것임\n'

In [26]:
while len(df1)/len(df) > 0.2:
    np.random.seed(42)
    random_number = np.random.randint(len(df1))
    df_id = df1.iloc[[random_number]]
    index = df_id.iloc[0,0]
    df3 = df1[df1['TRAVEL_ID'] == index]
    df1 = pd.merge(df3, df1, how = 'outer', indicator = True)
    df1 = df1.query('_merge =="right_only"').drop(columns = ['_merge'])
    # Train = Train.append(df3)
    Train = pd.concat([Train, df3])

In [27]:
print(len(Train)) # train set 길이
print(len(df1)) # test set 길이
print(len(df))
print(len(df1) / len(df))

18011
4351
22362
0.19457114748233612


## Train set에서 방문지에 대한 변수 생성
방문지마다 체류시간 평균, 추천의향의 평균, 재방문여부의 평균, 동반자 수의 평균, 재방문의향의 평균 산출

In [28]:
#새로운 데이터프레임 생성해서, 이 데이터프레임에 평균값을 추가한 새로운 Train set 생성할 것임

new_train = pd.DataFrame(columns = list(Train.columns) + ['RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
                                                          'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean',
                                                          'REVISIT_INTENTION_mean'])


for i in tqdm(list(Train['VISIT_AREA_NM'].unique())): #유니크한 관광지 목록 중에서
    df2 = Train[Train['VISIT_AREA_NM'] == i] # 특정 관광지에 간 모든 사람 뽑아서
    for j in ['RESIDENCE_TIME_MIN', 'RCMDTN_INTENTION', 'REVISIT_YN', 'TRAVEL_COMPANIONS_NUM', 'REVISIT_INTENTION']:
        #체류시간 평균 산출 
        globals()[str(j)+'_mean'] = df2[str(j)]
        globals()[str(j)+'_mean'] = np.mean(globals()[str(j)+'_mean'])
        #데이터프레임에 들어가게 값을 리스트 형태로 변환
        globals()[str(j)+'_mean'] = np.repeat(globals()[str(j)+'_mean'], len(df2)) 
        df2[str(j)+'_mean'] = globals()[str(j)+'_mean']
    #새로운 데이터프레임에 방문지별 평균값 대입
    new_train = pd.concat([new_train, df2], axis = 0)

100%|██████████| 8805/8805 [00:42<00:00, 208.35it/s]


In [29]:
#편의를 위해 유저별 정렬
new_train.sort_values(by = ['TRAVEL_ID'], axis = 0, inplace = True)

## DATA SET 저장

In [30]:
#train set 저장
new_train.to_csv(path + '/관광지 추천시스템 Trainset_B.csv', index = False)
#test set 저장
df1.to_csv(path + '/관광지 추천시스템 Testset_B.csv', index = False)

In [31]:
# 파일 불러오기
Train = pd.read_csv(path + '/관광지 추천시스템 Trainset_B.csv')
test = pd.read_csv(path + '/관광지 추천시스템 Testset_B.csv')

In [32]:
Train.dropna(inplace = True)
Train.reset_index(inplace = True, drop = True )

In [33]:
test.dropna(inplace = True)
test.reset_index(inplace = True, drop = True )

In [34]:
print(Train.shape)
print(test.shape)

(18011, 31)
(4351, 26)


# Train set 여행 방문지 필터링

## 5번 이상 방문한 곳에 대해서만 학습 / 테스트

In [39]:
count = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts()).reset_index()

In [41]:
count

VISIT_AREA_NM  count
0                       광안리해수욕장    104
1                       해운대해수욕장     80
2                           대릉원     78
3                          황련단길     77
4                        전주한옥마을     70
...                         ...    ...
8800                 거진전통시장 주차장      1
8801                     거진해수욕장      1
8802                    통영수산과학관      1
8803  바운스 트램펄린 파크 거제한 하벨 버티어 센터      1
8804           문의 청남대 휴게소 청주 방향      1

[8805 rows x 2 columns]

In [43]:
Train.reset_index(drop = True, inplace= True)
#5번 이상 방문한 곳으로만 필터링
count = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts())
count['places'] = count.index
### 여기 숫자 변경
five_places = list(count[count['count']>=5]['places']) 
###
for i in range(len(Train)):
    if Train['VISIT_AREA_NM'][i] not in five_places:
        Train = Train.drop([i], axis = 0)
Train.reset_index(drop = True, inplace = True)

In [44]:
#확인
count1 = pd.DataFrame(Train['VISIT_AREA_NM'].value_counts())
count1.groupby(['VISIT_AREA_NM'])['VISIT_AREA_NM'].count()

KeyError: 'Column not found: VISIT_AREA_NM'

In [47]:
Train.shape

(6826, 31)

In [48]:
print(Train.shape)
print(test.shape)

(6826, 31)
(4351, 26)


# Catboost 모델 기반 추천시스템 학습

In [49]:
#학습에 필요없는 feature 제거
Train.drop(['TRAVELER_ID', 'REVISIT_INTENTION',
            'RCMDTN_INTENTION','RESIDENCE_TIME_MIN', 'REVISIT_YN'], axis = 1, inplace = True)
test.drop(['TRAVELER_ID', 'REVISIT_INTENTION',
            'RCMDTN_INTENTION','RESIDENCE_TIME_MIN', 'REVISIT_YN'], axis = 1, inplace = True)

In [50]:
# 데이터 타입 변경
Train['VISIT_AREA_TYPE_CD'] = Train['VISIT_AREA_TYPE_CD'].astype('string')
test['VISIT_AREA_TYPE_CD'] = test['VISIT_AREA_TYPE_CD'].astype('string')

In [51]:
y_train = Train['DGSTFN']
X_train = Train.drop(['DGSTFN'], axis = 1)

## 초모수 조절
Cross Validation Set 생성 + Random Search 함수

train set의 feature, target, cv 개수를 입력하면 cross validaiton set을 생성해주는 함수 생성

최대한 많은 관광지 정보를 보존하기 위해 cv = 10 으로 설정

In [62]:
def cross_validation(X_train, y_train, cv, iteration,number, random_state): #X_train 데이터, y_train 데이터, cv 개수, random search 횟수, random_state

    X_train1 = X_train #변수 옮기기
    y_train1 = y_train #변수 옮기기
    for i in range(cv): #각 fold마다의 X_train, y_train 생성 (Train_1, Train_2, ... / target_1, target_2, ...)
        globals()['Train_'+str(i+1)] = pd.DataFrame(columns = list(X_train.columns))
        globals()['target_'+str(i+1)] = []
    print(str(cv)+'개의 fold를 생성중입니다.....')
    for i in tqdm(range(cv)):
        np.random.seed(random_state) #초기 시드 설정
        while (len(globals()['Train_'+str(i+1)]) / len(X_train)) < (1/cv): #1/cv 비율 만큼의 데이터가 모일 때까지
            random_number = np.random.randint(len(X_train1))
            df_id = X_train1.iloc[[random_number]]
            index = df_id.iloc[0,0] #랜덤하게 유저를 선택하고
            df1 = X_train1[X_train1['TRAVEL_ID'] == index] #그 유저가 갔던 모든 여행지 불러오고
            target_index = X_train1[X_train1['TRAVEL_ID'] == index].index
            X_train1 = pd.merge(df1, X_train1, how = 'outer', indicator = True)
            X_train1 = X_train1.query('_merge =="right_only"').drop(columns = ['_merge']) #기존 데이터프레임은 해당 유저 정보 삭제
            # globals()['Train_'+str(i+1)] = globals()['Train_'+str(i+1)].append(df1) #validation set에 유저의 X_train 삽입
            globals()['Train_'+str(i+1)] = pd.concat([globals()['Train_'+str(i+1)], df1])
            globals()['target_'+str(i+1)].extend(list(y_train[list(target_index)])) #유저의 X_train에 상응하는 y_train 삽입
            if len(X_train1) == 0: #기존 데이터프레임에 모든 유저정보가 사라지면 validation set 생성이 완료된 것이므로 정지
                break
    print(str(cv)+'개의 fold 생성이 완료되었습니다!')
    print('함수에서 설정한 초모수 범위 내에서 ' + str(cv)+'개의 validation 검정을 진행합니다...' )
    
    
    np.random.seed(random_state)
    initial = 0 
    for a in tqdm(range(iteration)):
        print(str(a+1) + "번째 초모수 조절치에 대한 학습을 진행합니다....")
        ##########여기에 원하는 hyperparameter 기입###########
        ######################################################
        n_estimators = np.random.choice(np.arange(700, 1301, 50))
        max_depth = np.random.choice(np.arange(5, 11, 1))
        subsample = np.random.choice(np.arange(0.75, 1.0001, 0.05))
        colsample_bylevel = np.random.choice(np.arange(0.8, 1.0001, 0.05))
        ######################################################
######################################################
        final_recall = [] # K개의 검증 성능이 들어갈 리스트

        for j in range(cv): #K개 fold중
            print(str(a+1) + '번째 초모수 조절치의' + str(j+1)+'번째 fold를 학습하고 있습니다....')
            #한 fold에 대해서 학습
            combine_df_list = list(range(1, (cv+1))) # 1부터 cv까지 숫자리스트 만들어서
            del combine_df_list[j] #숫자 하나를 지우고, 그 숫자가 있는 Train set을 Validation set으로 설정
            #예를 들어 1이 빠졌으면 Train_1이 validation set, Train_2, Train_3, ... 는 Train set
            X_new_train = pd.DataFrame(columns = list(globals()['Train_'+str(j+1)].columns))
            y_new_train = []
            for i in combine_df_list: #지운 숫자 외의 숫자가 있는 Train set들을 결합
                X_new_train = pd.concat([X_new_train, globals()['Train_'+str(i)]], axis = 0) #X_train 결합
                y_new_train.extend(globals()['target_'+str(i)]) #y_train 결합
            y_new_train = np.array(y_new_train).astype(float)
            X_new_train.drop(['TRAVEL_ID'], axis = 1, inplace = True) #필요 없는 컬럼 제거
            if 'DGSTFN' in list(X_new_train.columns): #global 함수에서 발생하는 오류 해결
                X_new_train.drop(['DGSTFN'], axis = 1, inplace = True)
            model = CatBoostRegressor(n_estimators = n_estimators,
                                  max_depth = max_depth,
                                  subsample = subsample,
                                  colsample_bylevel = colsample_bylevel,
                                  cat_features = ['VISIT_AREA_NM', 'SIDO', 'GUNGU','VISIT_AREA_TYPE_CD',
                                              'TRAVEL_MISSION_PRIORITY', 'AGE_GRP', 'GENDER'], 
                                  random_state = 42)
        ##############################################################################################

            model.fit(X_new_train, y_new_train) #########모델 적합

            #학습한 fold에 대한 test 값 도출
            recall_10_list = [] #validation set의 recall 측정값들이 들어갈 리스트
            #####################유저 정보##################################
            data = globals()['Train_'+str(j+1)][['TRAVEL_ID', 'SIDO', 'GUNGU', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
            data1 = pd.DataFrame(columns=['TRAVEL_ID', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'sido_gungu_list'])
            for i in list(data['TRAVEL_ID'].unique()):
                temp_df = data[data['TRAVEL_ID'] == i]
                temp_df1 = temp_df[['SIDO', 'GUNGU']] #각 유저별 방문한 시군구 확인
                temp_df1.reset_index(drop = True, inplace = True)
                sido_gungu_visit = []
                for k in range(len(temp_df1)):
                    sido_gungu_visit.append(temp_df1['SIDO'][k] + '+' + temp_df1['GUNGU'][k])
                sido_gungu_list = list(set(sido_gungu_visit))
                new = temp_df.drop(['SIDO', 'GUNGU'], axis = 1) #기존 시도, 군구 제외하고
                new = new.head(1)
                new['sido_gungu_list'] = str(sido_gungu_list)
                data1 = pd.concat([data1, new], axis = 0) #새로운 데이터프레임 생성 
            data1.reset_index(drop = True, inplace = True)
            ##########################여행지 정보################################
            info = X_new_train[['SIDO', 'VISIT_AREA_NM', 'GUNGU','VISIT_AREA_TYPE_CD','RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
            'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']]
            info.drop_duplicates(['VISIT_AREA_NM'], inplace = True)
            ###### 2회 이상 관광한 방문지 리스트 생성
            visiting_list = X_new_train[['VISIT_AREA_NM']] #train set에 있는 방문지에 대해서만 2회 이상 방문하였는지 확인
            visiting_list.reset_index(drop = True, inplace = True)
            #데이터 전처리
            dfdf = pd.DataFrame(visiting_list.value_counts(), columns = ['count'])
            dfdf['VISIT_AREA_NM'] = dfdf.index
            dfdf.reset_index(drop = True, inplace = True)
            for i in range(len(dfdf)):
                dfdf['VISIT_AREA_NM'][i] = str(dfdf['VISIT_AREA_NM'][i])
                dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i].replace("(","").replace(")","").replace(",","").replace("\''","")
                dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i][1:-1]
            #n회 이상 적용
            dfdf = dfdf[dfdf['count'] >= number] 
            visit_list = list(dfdf['VISIT_AREA_NM']) #visit_list에 2회 이상 방문지 리스트
            #방문지가 2회 이상 방문한 관광지 아니면 제거
            info.reset_index(drop = True, inplace = True)
            for i in range(len(info)):
                if info['VISIT_AREA_NM'][i] not in visit_list:
                    info = info.drop([i], axis = 0)
            info.reset_index(drop = True, inplace = True)
            ##########################모델 10개 관광지 추천############################
            result = []
            for i in range(len(data1)):
                #데이터

                final_df = pd.DataFrame(columns = ['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD',
                       'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                       'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                       'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                       'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
                       'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
                       'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']) #빈 데이터프레임에 내용 추가
                ####### 시/도 군/구 별 자료 수집
                temp = data1['sido_gungu_list'][i].replace("[","").replace("]","").replace("\'","").replace(", ",",")
                places_list = list(map(str, temp.split(",")))
                for q in places_list:
                    sido, gungu = map(str, q.split("+"))

                    info_df = info[(info['SIDO'] == sido) & (info['GUNGU'] == gungu)] 

                    info_df.drop(['SIDO'], inplace = True, axis = 1)
                    info_df.reset_index(inplace = True, drop = True)
                    data2 = data1.drop(['sido_gungu_list'], axis =1)
                    user_df = pd.DataFrame([data2.iloc[i].to_list()]*len(info_df), columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                        'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                        'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                        'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM'])
                    df = pd.concat([user_df, info_df], axis = 1)
                    df = df[['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD',
                   'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                   'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                   'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                   'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
                   'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
                   'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']] # 변수정렬
                    df['VISIT_AREA_TYPE_CD'] = df['VISIT_AREA_TYPE_CD'].astype('string')
                    final_df = pd.concat([final_df, df], axis = 0)
                final_df.reset_index(drop = True, inplace = True)
                final_df.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

                #모델 예측
                y_pred = model.predict(final_df)
                y_pred = pd.DataFrame(y_pred, columns = ['y_pred'])
                test_df1 = pd.concat([final_df, y_pred], axis = 1)
                test_df1.sort_values(by = ['y_pred'], axis = 0, ascending=False, inplace = True) # 예측치가 높은 순대로 정렬

                test_df1 = test_df1.iloc[0:10,] #상위 10개 관광지 추천

                visiting_candidates = list(test_df1['VISIT_AREA_NM']) # 모델이 추천한 관광지들을 리스트 형태로 변환

               # 유저정보와 추천 관광지
                test_df2 = test_df1[['SIDO','TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                    'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                    'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                    'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
                if len(test_df2) == 0:
                    rec = []
                    result.append(rec)
                else:

                    rec = test_df2.iloc[0].to_list()

                    rec.append(visiting_candidates)

                    result.append(rec)
            final_df = pd.DataFrame(result,
                                columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                                'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                                'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                                'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'recommend_result_place'])
            final_df = final_df[['recommend_result_place']]
            travel_id = data1[['TRAVEL_ID']]
            travel_id.reset_index(drop = True, inplace = True)
            final_df = pd.concat([travel_id, final_df], axis = 1)

            #추천지 10개 미만인 여행 ID확인
            travel_id_list = []
            for i in range(len(final_df)):
                recommend_list = final_df['recommend_result_place'][i]
                if str(recommend_list).count(',') < 9:
                    travel_id_list.append(final_df['TRAVEL_ID'][i])
                if pd.isna(str(recommend_list)):
                    travel_id_list.append(final_df['TRAVEL_ID'][i])
            ## 군구 리스트
            places = list(set(globals()['Train_'+str(j+1)]['GUNGU']))
            for i in range(len(places)):
                if places[i][-1] == '구' or places[i][-1] == '시' or places[i][-1] == '군':
                    places[i] = places[i][:-1]

            ###############################################################
            ######## 최종 성능 평가 #########################################
            #########################################################
            visit_list = list(info['VISIT_AREA_NM'])
            globals()['Train_'+str(j+1)]['DGSTFN'] = globals()['target_'+str(j+1)]



            for i in list(globals()['Train_'+str(j+1)]['TRAVEL_ID'].unique()):

                #추천한 방문지가 10개 미만이면 0
                if i in travel_id_list:
                    recall_10_list.append(0)
                    continue

                satisfied = globals()['Train_'+str(j+1)][globals()['Train_'+str(j+1)]['TRAVEL_ID'] == i] #실제(y_actual) 관광객이 만족한 관광지
                satisfied.reset_index(drop = True, inplace = True) 


                satisfied1 = satisfied[satisfied['DGSTFN'] >=4 ] #만족의 기준은 4이상 일때만 만족이라고 정의
                if len(satisfied1) == 0: # 유저가 만족한 관광지가 하나도 없으면 recall@10은 어차피 0
                    recall_10_list.append(0)
                    continue
                else:
                    item_list = satisfied1['VISIT_AREA_NM']


                item_list = list(set(item_list))


            #final_df의 추천지 10개랑 비교

                recommend_list = final_df[final_df['TRAVEL_ID'] == i]['recommend_result_place'] #모델 추천 관광지 30개

                summ = 0
                for n in item_list:
                    word_list = list(n.split(' '))
                    if word_list[-1][-1] == '점': #지점명 삭제
                        del word_list[-1]
                    for o in word_list:
                        if o in places:#장소에 군/구 명 있으면 아무것도 하지 않고 스킵
                            pass
                        else:
                            for p in recommend_list: #장소에 교차어 있으면 해당 장소는 방문했다고 인식하기
                                if o in str(p) :
                                    summ += 1
                recall10_for_1user = summ / min(10, len(satisfied1)) #recall@10 산식
                if recall10_for_1user > 1:
                    recall10_for_1user = 1
                recall_10_list.append(recall10_for_1user)
            globals()['Train_'+str(j+1)].drop(['DGSTFN'], axis = 1, inplace = True) #globals 함수 오류 해결하기 위한 코드
            
            recall_for_one_cv = sum(recall_10_list) / len(recall_10_list) #한 fold에 대한 recall@10값 추출
                
            final_recall.append(recall_for_one_cv)

        recallat10 = sum(final_recall) / len(final_recall)
        print('이번 결과는:', recallat10)
        ###################### hyperparameter 바꾸면 여기도 수정해야 ######################
        ###################################################################################
        print('이번 결과의 parameter은: ', 'n_estimators:', n_estimators, 'max_depth:', max_depth, 
                  'subsample:', subsample, 'colsample_bylevel:', colsample_bylevel)
        if recallat10 > initial:
            initial = recallat10
            print('신기록!:', initial)
            print('n_estimators:', n_estimators, 'max_depth:', max_depth, 
                  'subsample:', subsample, 'colsample_bylevel:', colsample_bylevel)
            final_estimator = n_estimators
            final_max_depth = max_depth
            final_subsample = subsample
            final_colsample_bylevel = colsample_bylevel
         #####################################################################################
    print('최종 parameter은 :',  final_estimator, 'max_depth:', final_max_depth, 
                  'subsample:', final_subsample, 'colsample_bylevel:', final_colsample_bylevel)
    return(initial)

In [63]:
#초모수 조절
cross_validation(X_train, y_train, cv = 10, iteration = 10, number = 5, random_state = 42)

10개의 fold를 생성중입니다.....


100%|██████████| 10/10 [01:31<00:00,  9.16s/it]


10개의 fold 생성이 완료되었습니다!
함수에서 설정한 초모수 범위 내에서 10개의 validation 검정을 진행합니다...


  0%|          | 0/10 [00:00<?, ?it/s]

1번째 초모수 조절치에 대한 학습을 진행합니다....
1번째 초모수 조절치의1번째 fold를 학습하고 있습니다....
Learning rate set to 0.054542
0:	learn: 0.7821640	total: 197ms	remaining: 3m 16s
1:	learn: 0.7815114	total: 259ms	remaining: 2m 9s
2:	learn: 0.7804957	total: 324ms	remaining: 1m 47s
3:	learn: 0.7801642	total: 388ms	remaining: 1m 36s
4:	learn: 0.7797154	total: 453ms	remaining: 1m 30s
5:	learn: 0.7791468	total: 514ms	remaining: 1m 25s
6:	learn: 0.7785982	total: 598ms	remaining: 1m 24s
7:	learn: 0.7778314	total: 671ms	remaining: 1m 23s
8:	learn: 0.7773556	total: 735ms	remaining: 1m 20s
9:	learn: 0.7773140	total: 751ms	remaining: 1m 14s
10:	learn: 0.7768280	total: 811ms	remaining: 1m 12s
11:	learn: 0.7764639	total: 878ms	remaining: 1m 12s
12:	learn: 0.7757891	total: 940ms	remaining: 1m 11s
13:	learn: 0.7752322	total: 999ms	remaining: 1m 10s
14:	learn: 0.7750098	total: 1.06s	remaining: 1m 9s
15:	learn: 0.7740484	total: 1.12s	remaining: 1m 8s
16:	learn: 0.7735581	total: 1.18s	remaining: 1m 8s
17:	learn: 0.7728718	total: 1.24s	

...

No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded


10번째 초모수 조절치의10번째 fold를 학습하고 있습니다....
Learning rate set to 0.045511
0:	learn: 0.7909305	total: 43ms	remaining: 53.7s
1:	learn: 0.7900309	total: 106ms	remaining: 1m 5s
2:	learn: 0.7894458	total: 160ms	remaining: 1m 6s
3:	learn: 0.7889612	total: 211ms	remaining: 1m 5s
4:	learn: 0.7887910	total: 258ms	remaining: 1m 4s
5:	learn: 0.7881524	total: 309ms	remaining: 1m 3s
6:	learn: 0.7875357	total: 360ms	remaining: 1m 3s
7:	learn: 0.7869029	total: 408ms	remaining: 1m 3s
8:	learn: 0.7866712	total: 458ms	remaining: 1m 3s
9:	learn: 0.7860187	total: 506ms	remaining: 1m 2s
10:	learn: 0.7854056	total: 556ms	remaining: 1m 2s
11:	learn: 0.7848109	total: 612ms	remaining: 1m 3s
12:	learn: 0.7843614	total: 662ms	remaining: 1m 3s
13:	learn: 0.7841416	total: 711ms	remaining: 1m 2s
14:	learn: 0.7837258	total: 757ms	remaining: 1m 2s
15:	learn: 0.7833089	total: 807ms	remaining: 1m 2s
16:	learn: 0.7830184	total: 860ms	remaining: 1m 2s
17:	learn: 0.7821801	total: 907ms	remaining: 1m 2s
18:	learn: 0.7818619	tota

No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
No objects 

이번 결과는: 0.2615250220143607
이번 결과의 parameter은:  n_estimators: 1250 max_depth: 8 subsample: 0.75 colsample_bylevel: 0.9000000000000001
최종 parameter은 : 850 max_depth: 7 subsample: 1.0000000000000002 colsample_bylevel: 1.0000000000000002


0.27010160972183256

## Catboost 적합

범주형 변수 목록

VISIT_AREA_NM 방문지

SIDO 시도

GUNGU 군구

VISIT_AREA_CD 관광지 종류 코드

TRAVEL_MISSION_PRIORITY 유저가 설정한 본인의 미션 중 첫번째

AGE_GRP 연령대

GENDER 성별

In [66]:
y_train = Train['DGSTFN']
X_train = Train.drop(['DGSTFN', 'TRAVEL_ID'], axis = 1)

In [67]:
model = CatBoostRegressor(n_estimators = 1250, max_depth = 8, subsample = 1.0000000000000002, 
                          colsample_bylevel = 1.0000000000000002,
    cat_features = ['VISIT_AREA_NM', 'SIDO', 'GUNGU','VISIT_AREA_TYPE_CD',
                                                  'TRAVEL_MISSION_PRIORITY', 'AGE_GRP', 'GENDER'], random_state = 42)
model.fit(X_train, y_train)

Learning rate set to 0.046258
0:	learn: 0.7823902	total: 74.3ms	remaining: 1m 32s
1:	learn: 0.7791357	total: 127ms	remaining: 1m 19s
2:	learn: 0.7764579	total: 166ms	remaining: 1m 9s
3:	learn: 0.7736536	total: 225ms	remaining: 1m 10s
4:	learn: 0.7703922	total: 305ms	remaining: 1m 16s
5:	learn: 0.7678924	total: 334ms	remaining: 1m 9s
6:	learn: 0.7656890	total: 385ms	remaining: 1m 8s
7:	learn: 0.7632378	total: 446ms	remaining: 1m 9s
8:	learn: 0.7618811	total: 464ms	remaining: 1m 3s
9:	learn: 0.7596176	total: 516ms	remaining: 1m 4s
10:	learn: 0.7575401	total: 550ms	remaining: 1m 1s
11:	learn: 0.7553451	total: 611ms	remaining: 1m 3s
12:	learn: 0.7531765	total: 665ms	remaining: 1m 3s
13:	learn: 0.7516624	total: 717ms	remaining: 1m 3s
14:	learn: 0.7496658	total: 775ms	remaining: 1m 3s
15:	learn: 0.7478285	total: 831ms	remaining: 1m 4s
16:	learn: 0.7464221	total: 886ms	remaining: 1m 4s
17:	learn: 0.7448892	total: 937ms	remaining: 1m 4s
18:	learn: 0.7433198	total: 988ms	remaining: 1m 4s
19:	le

In [68]:
now = time
print(now.strftime('%Y-%m-%d %H:%M:%S'))

2024-08-03 09:08:39


In [69]:
joblib.dump(model,path + '/catboost_model_B.pkl')

['./bami/data/total//catboost_model_B.pkl']

In [70]:
modelb = joblib.load(path + '/catboost_model_B.pkl')
testb = pd.read_csv(path + '/관광지 추천시스템 Testset_B.csv')
trainb = pd.read_csv(path + '/관광지 추천시스템 Trainset_B.csv')

# Test B

## 모델의 10개 관광지 후보 불러오기

### 유저 정보

In [71]:
y_testb = testb['DGSTFN']
X_testb = testb.drop(['DGSTFN'], axis = 1)

In [72]:
#유저정보
data = testb[['TRAVEL_ID', 'SIDO', 'GUNGU', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]

In [73]:
#내가 간 시도 군구 리스트:
data1 = pd.DataFrame(columns=['TRAVEL_ID', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'sido_gungu_list'])
for i in tqdm(list(data['TRAVEL_ID'].unique())):
    temp_df = data[data['TRAVEL_ID'] == i]
    temp_df1 = temp_df[['SIDO', 'GUNGU']] #각 유저별 방문한 시군구 확인
    temp_df1.reset_index(drop = True, inplace = True)
    sido_gungu_visit = []
    for j in range(len(temp_df1)):
        sido_gungu_visit.append(temp_df1['SIDO'][j] + '+' + temp_df1['GUNGU'][j])
    sido_gungu_list = list(set(sido_gungu_visit))
    new = temp_df.drop(['SIDO', 'GUNGU'], axis = 1) #기존 시도, 군구 제외하고
    new = new.head(1)
    new['sido_gungu_list'] = str(sido_gungu_list)
    data1 = pd.concat([data1, new], axis = 0) #새로운 데이터프레임 생성        
    

100%|██████████| 2082/2082 [00:03<00:00, 663.28it/s]


In [74]:
#유저 정보 저장
data1.reset_index(drop = True, inplace = True)
data1.to_csv(path + '/관광지 추천시스템 Testset_B- 유저 정보.csv', index=False)

### 여행지 정보

In [75]:
#여행지 정보
info = trainb[['SIDO', 'VISIT_AREA_NM', 'GUNGU','VISIT_AREA_TYPE_CD','RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean',
            'REVISIT_YN_mean', 'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']]
info.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

2회 이상 방문지 리스트 뽑아서 여행지 정보에 없는 것 제거

In [76]:
###### 2회 이상 관광한 방문지 리스트 생성
visiting_list = trainb[['VISIT_AREA_NM']] #train set에 있는 방문지에 대해서만 2회 이상 방문하였는지 확인
visiting_list.reset_index(drop = True, inplace = True)
#데이터 전처리
dfdf = pd.DataFrame(visiting_list.value_counts(), columns = ['count'])
dfdf['VISIT_AREA_NM'] = dfdf.index
dfdf.reset_index(drop = True, inplace = True)
for i in range(len(dfdf)):
    dfdf['VISIT_AREA_NM'][i] = str(dfdf['VISIT_AREA_NM'][i])
    dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i].replace("(","").replace(")","").replace(",","").replace("\''","")
    dfdf['VISIT_AREA_NM'][i] = dfdf['VISIT_AREA_NM'][i][1:-1]
#5회 이상 적용
dfdf = dfdf[dfdf['count'] >= 5]  
visit_list = list(dfdf['VISIT_AREA_NM']) #visit_list에 5회 이상 방문지 리스트

In [77]:
#방문지가 5회 이상 방문한 관광지 아니면 제거
info.reset_index(drop = True, inplace = True)
for i in tqdm(range(len(info))):
    if info['VISIT_AREA_NM'][i] not in visit_list:
        info = info.drop([i], axis = 0)
info.reset_index(drop = True, inplace = True)

100%|██████████| 8805/8805 [00:03<00:00, 2319.88it/s]


In [78]:
#여행자 정보 저장
info.reset_index(drop = True, inplace = True)
info.to_csv(path + '/관광지 추천시스템 Testset_B- 여행지 정보.csv', index=False)

### 모델의 10개 추천 관광지 목록 제작 코드

In [79]:
data = pd.read_csv(path + '/관광지 추천시스템 Testset_B- 유저 정보.csv')
info = pd.read_csv(path + '/관광지 추천시스템 Testset_B- 여행지 정보.csv')

In [80]:
result = []
for i in tqdm(range(len(data1))):
    #데이터
    
    final_df = pd.DataFrame(columns = ['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD',
           'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
           'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
           'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
           'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
           'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
           'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']) #빈 데이터프레임에 내용 추가
    ####### 시/도 군/구 별 자료 수집
    temp = data1['sido_gungu_list'][i].replace("[","").replace("]","").replace("\'","").replace(", ",",")
    places_list = list(map(str, temp.split(",")))
    for q in places_list:
        sido, gungu = map(str, q.split("+"))

        info_df = info[(info['SIDO'] == sido) & (info['GUNGU'] == gungu)] 

        info_df.drop(['SIDO'], inplace = True, axis = 1)
        info_df.reset_index(inplace = True, drop = True)
        data2 = data1.drop(['sido_gungu_list'], axis =1)
        user_df = pd.DataFrame([data2.iloc[i].to_list()]*len(info_df), columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM'])
        df = pd.concat([user_df, info_df], axis = 1)
        df = df[['VISIT_AREA_NM', 'SIDO', 'GUNGU', 'VISIT_AREA_TYPE_CD',
       'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
       'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
       'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
       'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM',
       'RESIDENCE_TIME_MIN_mean', 'RCMDTN_INTENTION_mean', 'REVISIT_YN_mean',
       'TRAVEL_COMPANIONS_NUM_mean', 'REVISIT_INTENTION_mean']] # 변수정렬
        df['VISIT_AREA_TYPE_CD'] = df['VISIT_AREA_TYPE_CD'].astype('string')
        final_df = pd.concat([final_df, df], axis = 0)
    final_df.reset_index(drop = True, inplace = True)
    final_df.drop_duplicates(['VISIT_AREA_NM'], inplace = True)

    #모델 예측
    y_pred = modelb.predict(final_df)
    y_pred = pd.DataFrame(y_pred, columns = ['y_pred'])
    test_df1 = pd.concat([final_df, y_pred], axis = 1)
    test_df1.sort_values(by = ['y_pred'], axis = 0, ascending=False, inplace = True) # 예측치가 높은 순대로 정렬

    test_df1 = test_df1.iloc[0:10,] #상위 10개 관광지 추천

    visiting_candidates = list(test_df1['VISIT_AREA_NM']) # 모델이 추천한 관광지들을 리스트 형태로 변환

# 유저정보와 추천 관광지
    test_df2 = test_df1[['SIDO','TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                        'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                        'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                        'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM']]
    if len(test_df2) == 0:
        rec = []
        result.append(rec)
    else:
        
        rec = test_df2.iloc[0].to_list()

        rec.append(visiting_candidates)

        result.append(rec)



  7%|▋         | 136/2082 [00:01<00:16, 117.35it/s]No objects info loaded
No objects info loaded
No objects info loaded
  8%|▊         | 173/2082 [00:01<00:16, 116.02it/s]No objects info loaded
No objects info loaded
  9%|▉         | 185/2082 [00:01<00:16, 114.86it/s]No objects info loaded
No objects info loaded
 11%|█▏        | 237/2082 [00:02<00:15, 117.01it/s]No objects info loaded
No objects info loaded
 13%|█▎        | 262/2082 [00:02<00:15, 119.37it/s]No objects info loaded
No objects info loaded
No objects info loaded
 19%|█▉        | 394/2082 [00:03<00:13, 120.95it/s]No objects info loaded
No objects info loaded
 20%|█▉        | 407/2082 [00:03<00:13, 123.25it/s]No objects info loaded
No objects info loaded
No objects info loaded
No objects info loaded
 20%|██        | 422/2082 [00:03<00:12, 128.72it/s]No objects info loaded
No objects info loaded
 22%|██▏       | 450/2082 [00:03<00:12, 132.36it/s]No objects info loaded
No objects info loaded
No objects info loaded
 24%|██▎    

In [81]:
final_df = pd.DataFrame(result,
                            columns = ['SIDO', 'TRAVEL_MISSION_PRIORITY', 'GENDER', 'AGE_GRP', 'INCOME',
                            'TRAVEL_STYL_1', 'TRAVEL_STYL_2', 'TRAVEL_STYL_3', 'TRAVEL_STYL_4',
                            'TRAVEL_STYL_5', 'TRAVEL_STYL_6', 'TRAVEL_STYL_7', 'TRAVEL_STYL_8',
                            'TRAVEL_MOTIVE_1', 'TRAVEL_NUM', 'TRAVEL_COMPANIONS_NUM', 'recommend_result_place'])
final_df = final_df[['recommend_result_place']]
travel_id = data1[['TRAVEL_ID']]
travel_id.reset_index(drop = True, inplace = True)
final_df = pd.concat([travel_id, final_df], axis = 1)

In [82]:
#output_df 저장
final_df.to_csv(path + '/관광지 추천시스템 Testset- OUTPUT_B.csv', index=False)
#output_df 불러오기
final_df = pd.read_csv(path + '/관광지 추천시스템 Testset- OUTPUT_B.csv')

## 실제 유저가 다녀온 관광지랑 비교하여 Recall@10 산출

In [83]:
final_df

TRAVEL_ID                             recommend_result_place
0     e_e000004  ['효원공원 월화원', '갤러리아백화점 광교점', '일월 수목원', '행리단길', ...
1     e_e000009                             ['농협안성팜랜드', '스타필드 안성']
2     e_e000011  ['광화문광장', '조계사', '청와대 본관', '창경궁', '통인시장', '청계천...
3     e_e000014   ['에버랜드', '롯데 프리미엄 아울렛 기흥점', '이케아 기흥점', '캐리비안베이']
4     e_e000016         ['서울 식물원', '현대 프리미엄 아울렛 김포점', '롯데몰 김포공항점']
...         ...                                                ...
2077  g_g013090  ['현충사', '신정호 관광단지', '은행나무 길', '신정호', '외암민속마을',...
2078  g_g013095                    ['이응 다리', '국립세종수목원', '세종 호수공원']
2079  g_g013102  ['정림사지박물관', '국립부여박물관', '정림사지박물관 정림사지 5층 석탑', '...
2080  g_g013113  ['한빛탑 광장', '한밭수목원', '장태산자연휴양림', '대전 신세계', '천연기...
2081  h_h001459  ['단양강잔도', '카페 산', '사인암', '구인사', '만천하 스카이워크', '...

[2082 rows x 2 columns]

In [84]:
#추천지 10개 미만인 여행 ID확인
travel_id_list = []
for i in tqdm(range(len(final_df))):
    recommend_list = final_df['recommend_result_place'][i]
    if pd.isna(recommend_list):
        travel_id_list.append(final_df['TRAVEL_ID'][i])
        continue
    if recommend_list.count(',') < 9:
        travel_id_list.append(final_df['TRAVEL_ID'][i])

100%|██████████| 2082/2082 [00:00<00:00, 150860.17it/s]


In [85]:
#군/군 리스트 출력
## 이 부분 해결 하기 위해서 군/구 목록 places라는 변수에 뽑아오기
'''
4. 성능을 올리기 위해 다음과 같은 추가 방법 도입:
- 아무래도 사람이 수기로 데이터를 입력하다 보니까 유사/동일 장소를 갔음에도 컴퓨터는 다른 장소로 인식 
    -ex1: ’파라다이스시티‘와 ’파라다이스시티 주차장‘을 다른 장소로 인식
    -ex2: ‘국립중앙박물관 특별전시관’과 ‘국립중앙박물관’을 다른 장소로 인식
- 그러므로 ‘모델이 추천한 추천지 10개’와 ‘유저가 만족한다고 했던 곳’을 단어 별로 쪼개서 공통어가 있으면 교집합 개수에 추가
    -ex1: ‘파라다이스시티’와 ‘파라다이스시티 주차장’은 ‘파라다이스시티’라는 공통어가 있으므로 교집합 개수에 추가
    -ex2: ‘국립중앙박물관 특별전시관’과 ‘국립중앙박물관’은 ‘국립중앙박물관’이라는 공통어가 있으므로 교집합 개수에 추가
- ‘파주점’, ‘하남점’ 등 지점명이 공통어가 되는 경우 배제
    -ex1: ‘롯데프리미엄아울렛 파주점'이라는 장소가 있을 때, 마지막 단어의 마지막 글자가 '점'일 경우에 마지막 글자를 제거 (공통어 비교 시 '롯데프리미엄아울렛'만 비교)
- 유저가 방문한 장소에 군/구가 공통어가 되는 경우 배제
    -ex1: 유저가 방문한 '스타필드 고양'은 ’스타필드‘, ’고양‘으로 나누어지는데, '고양'이라는 군/구 명을 제거해서 ’고양 어울림누리‘ 같은 장소와 교차어로 포함되지 않도록 함
'''
places = list(set(X_testb['GUNGU']))
for i in range(len(places)):
    if places[i][-1] == '구' or places[i][-1] == '시' or places[i][-1] == '군':
        places[i] = places[i][:-1]

In [86]:
#유저가 다녀온 관광지 중에서 만족도가 4이상인 관광지 목록
recall_10_list = []
visit_list = list(info['VISIT_AREA_NM'])
for i in tqdm(list(testb['TRAVEL_ID'].unique())):
    
    #추천한 방문지가 10개 미만이면 0
    if i in travel_id_list:
        recall_10_list.append(0)
        continue
    
    satisfied = testb[testb['TRAVEL_ID'] == i] #실제(y_actual) 관광객이 만족한 관광지
    satisfied.reset_index(drop = True, inplace = True) 
    '''
    #2회 이상 방문한 곳에 대해서만 확인
    for c in range(len(satisfied)):
        if satisfied['VISIT_AREA_NM'][c] not in visit_list:
            satisfied = satisfied.drop([c], axis = 0)
    satisfied.reset_index(drop = True, inplace = True)    
    if len(satisfied) == 0:
        recall_10_list.append(0)
        continue
    '''
    satisfied1 = satisfied[satisfied['DGSTFN'] >=4 ] #만족의 기준은 4이상 일때만 만족이라고 정의
    if len(satisfied1) == 0: # 유저가 만족한 관광지가 하나도 없으면 recall@10은 어차피 0
        recall_10_list.append(0)
        continue
    else:
        item_list = satisfied1['VISIT_AREA_NM']
                
                
    item_list = list(set(item_list))
    

#final_df의 추천지 10개랑 비교
    recommend_list = final_df[final_df['TRAVEL_ID'] == i]['recommend_result_place'] #모델 추천 관광지 30개

    summ = 0
    for n in item_list:
        word_list = list(n.split(' '))
        if word_list[-1][-1] == '점': #지점명 삭제
            del word_list[-1]
        for o in word_list:
            if o in places:#장소에 군/구 명 있으면 아무것도 하지 않고 스킵
                pass
            else:
                for p in recommend_list: #장소에 교차어 있으면 해당 장소는 방문했다고 인식하기
                    if o in str(p) :
                        summ += 1
    recall10_for_1user = summ / min(10, len(satisfied1)) #recall@10 산식
    if recall10_for_1user > 1:
        recall10_for_1user = 1
    recall_10_list.append(recall10_for_1user)

100%|██████████| 2082/2082 [00:00<00:00, 3161.70it/s]


In [87]:
now = time
print(now.strftime('%Y-%m-%d %H:%M:%S'))

2024-08-03 09:09:50


In [88]:
#recall@10 구하기 
np.mean(recall_10_list)

0.22552890993092722

In [89]:
recall_10_list

[0.3333333333333333,
 0,
 0.0,
 0,
 0,
 0.5,
 0,
 0,
 1.0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.75,
 0.3,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1.0,
 0,
 0,
 0.0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.25,
 0.42857142857142855,
 0,
 0,
 0.3333333333333333,
 0,
 0,
 0,
 1,
 0.6666666666666666,
 0,
 0,
 0,
 0.3333333333333333,
 0,
 0,
 0,
 0,
 0,
 0,
 0.6666666666666666,
 0,
 0,
 0.75,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.6,
 0.0,
 1.0,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.5,
 0,
 0,
 0,
 0,
 0,
 0.5,
 0,
 1.0,
 0,
 0.0,
 0,
 0,
 1,
 0.3333333333333333,
 0,
 1,
 0.25,
 0.0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.6666666666666666,
 0,
 0,
 0,
 0,
 0,
 0,
 0.0,
 0,
 0.4,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1.0,
 0,
 0,
 0,
 0.5,
 0,
 0,
 0,
 0,
 0.0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0.5,
 0,
 0,
 0.5,
 0,
 0,
 0,
 1.0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.5,
 0,
 0,
 0.3333333333333333,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0.666666666666666